# 1. Introducción: Problema empresarial
    
En este proyecto trataremos de encontrar una ubicación óptima para un restaurante. En concreto, este informe irá dirigido a los interesados en abrir un restaurante japonés en la ciudad de Nueva York, Estados Unidos.
Dado que hay muchos restaurantes en Nueva York, trataremos de detectar ubicaciones que no estén rodeadas de varios restaurantes. También nos interesan especialmente las zonas que no tengan restaurantes japoneses en las inmediaciones. También preferimos ubicaciones lo más cerca posible del centro de la ciudad, suponiendo que se cumplan las dos primeras condiciones.

Utilizaremos nuestras habilidades en ciencia de datos para localizar los barrios más prometedores basándonos en estos criterios. Las ventajas de cada zona se expresarán claramente para que los interesados puedan elegir la mejor ubicación final.

# 2. Datos:

A partir de la definición de nuestro problema, los factores que influirán en nuestra decisión son:

1.- Número de restaurantes existentes en el barrio (cualquier tipo de restaurante)

2.- Número de restaurantes japoneses en el barrio y distancia a los mismos, si los hay

3.- Distancia del barrio al centro de la ciudad

Necesitaremos datos sobre diferentes restaurantes en diferentes barrios en específico. Para obtener esa información capturaremos las direcciones de los barrios en sus valores equivalentes de latitud y longitud, luego utilizaremos la información de localización de "Foursquare" para explorar los barrios de la ciudad de Nueva York. Foursquare es un proveedor de datos de localización con información sobre todo tipo de locales y eventos dentro de un área de interés. Dicha información incluye nombres de locales, ubicaciones, menús e incluso fotos. Como tal, la plataforma de localización de Foursquare se utilizará como única fuente de datos, ya que toda la información necesaria indicada puede obtenerse a través de la API. Por otro lado, se utilizará la función de exploración para obtener la lista de los restaurantes en cada barrio, y luego se agruparán los barrios en clusters mediante el algoritmo de k-means. Por último, se utilizará la biblioteca Folium para visualizar los barrios y restaurantes de la ciudad de Nueva York.

Antes de obtener los datos y empezar a explorarlos, vamos a descargar todas las dependencias que necesitaremos.

In [178]:
!pip install geocoder
!pip install folium
!pip install shapely
!pip install pyproj

In [179]:
import pandas as pd # library for data analsysis
import requests # library to handle requests
import numpy as np # library to handle data in a vectorized manner
import geocoder
import folium # map rendering library
import matplotlib.cm as cm # Matplotlib and associated plotting modules
import matplotlib.colors as colors # Matplotlib and associated plotting modules
import json # library to handle JSON files

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
from sklearn.cluster import KMeans # import k-means from clustering stage
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from bs4 import BeautifulSoup

import shapely.geometry
from pyproj import Transformer 
import math

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

print("All Required Libraries Imported!")

All Required Libraries Imported!


#### Descargar y explorar el conjunto de datos:

Se tiene un total de 5 distritos y 306 barrios. Para segmentar los barrios y explorarlos, necesitaremos esencialmente un conjunto de datos que contenga los 5 distritos y los barrios que existen en cada uno de ellos, así como las coordenadas de latitud y longitud de cada barrio.

Ejecutando el comando wget se puede acceder a los datos.

In [180]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


#### Cargar y explorar los datos:

A continuación, vamos a cargar los datos.

In [181]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Todos los datos relevantes están en la clave de características, que es básicamente una lista de los barrios. Así que vamos a definir una nueva variable que incluya estos datos.

In [182]:
neighborhoods_data = newyork_data['features']

#### Transformar los datos en un dataframe de pandas:

La siguiente tarea es esencialmente transformar estos datos de diccionarios Python anidados en un dataframe de pandas. Así que vamos a empezar por crear un dataframe vacío.

In [183]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

A continuación, vamos a recorrer los datos y a rellenar el marco de datos fila a fila.

In [184]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

El dataframe resultante.

In [185]:
neighborhoods

Borough               Neighborhood   Latitude  Longitude
0            Bronx                  Wakefield  40.894705 -73.847201
1            Bronx                 Co-op City  40.874294 -73.829939
2            Bronx                Eastchester  40.887556 -73.827806
3            Bronx                  Fieldston  40.895437 -73.905643
4            Bronx                  Riverdale  40.890834 -73.912585
5            Bronx                Kingsbridge  40.881687 -73.902818
6        Manhattan                Marble Hill  40.876551 -73.910660
7            Bronx                   Woodlawn  40.898273 -73.867315
8            Bronx                    Norwood  40.877224 -73.879391
9            Bronx             Williamsbridge  40.881039 -73.857446
10           Bronx                 Baychester  40.866858 -73.835798
11           Bronx             Pelham Parkway  40.857413 -73.854756
12           Bronx                City Island  40.847247 -73.786488
13           Bronx               Bedford Park  40.870185 -73.885512
14           Bronx         University Heights  40.855727 -73.910416
15           Bronx             Morris Heights  40.847898 -73.919672
16           Bronx                    Fordham  40.860997 -73.896427
17           Bronx               East Tremont  40.842696 -73.887356
18           Bronx                 West Farms  40.839475 -73.877745
19           Bronx               High  Bridge  40.836623 -73.926102
20           Bronx                    Melrose  40.819754 -73.909422
21           Bronx                 Mott Haven  40.806239 -73.916100
22           Bronx                Port Morris  40.801664 -73.913221
23           Bronx                   Longwood  40.815099 -73.895788
24           Bronx                Hunts Point  40.809730 -73.883315
25           Bronx                 Morrisania  40.823592 -73.901506
26           Bronx                  Soundview  40.821012 -73.865746
27           Bronx               Clason Point  40.806551 -73.854144
28           Bronx                Throgs Neck  40.815109 -73.816350
29           Bronx               Country Club  40.844246 -73.824099
30           Bronx                Parkchester  40.837938 -73.856003
31           Bronx         Westchester Square  40.840619 -73.842194
32           Bronx                   Van Nest  40.843608 -73.866299
33           Bronx                Morris Park  40.847549 -73.850402
34           Bronx                    Belmont  40.857277 -73.888452
35           Bronx             Spuyten Duyvil  40.881395 -73.917190
36           Bronx            North Riverdale  40.908543 -73.904531
37           Bronx                 Pelham Bay  40.850641 -73.832074
38           Bronx              Schuylerville  40.826580 -73.826203
39           Bronx             Edgewater Park  40.821986 -73.813885
40           Bronx                Castle Hill  40.819014 -73.848027
41           Bronx                  Olinville  40.871371 -73.863324
42           Bronx             Pelham Gardens  40.862966 -73.841612
43           Bronx                  Concourse  40.834284 -73.915589
44           Bronx                  Unionport  40.829774 -73.850535
45           Bronx                   Edenwald  40.884561 -73.848083
46        Brooklyn                  Bay Ridge  40.625801 -74.030621
47        Brooklyn                Bensonhurst  40.611009 -73.995180
48        Brooklyn                Sunset Park  40.645103 -74.010316
49        Brooklyn                 Greenpoint  40.730201 -73.954241
50        Brooklyn                  Gravesend  40.595260 -73.973471
51        Brooklyn             Brighton Beach  40.576825 -73.965094
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438
54        Brooklyn                   Flatbush  40.636326 -73.958401
55        Brooklyn              Crown Heights  40.670829 -73.943291
56        Brooklyn              East Flatbush  40.641718 -73.936103
57        Brooklyn                 Kensington  40.642382 -73.980421

El conjunto de datos tiene los 5 distritos y los 306 barrios.

In [186]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Se utiliza la biblioteca geopy para obtener los valores de latitud y longitud de la ciudad de Nueva York:

Para definir una instancia del geocodificador, necesitamos definir un user_agent. Llamaremos a nuestro agente ny_explorer, como se muestra a continuación.

In [187]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


Para calcular con precisión las distancias, debemos crear nuestra cuadrícula de ubicaciones en un sistema de coordenadas cartesianas 2D que nos permita calcular las distancias en metros (no en grados de latitud/longitud). Luego proyectaremos esas coordenadas a grados de latitud/longitud para mostrarlas en el mapa de Folium. Así que vamos a crear funciones para convertir entre el sistema de coordenadas esféricas WGS84 (grados de latitud/longitud) y el sistema de coordenadas cartesianas UTM (coordenadas X/Y en metros).

In [188]:
def lonlat_to_xy(lon, lat):
    transproj = Transformer.from_crs({"proj":'latlong', "datum":'WGS84'}, {"proj":'utm', "zone":'18', "datum":'WGS84'})
    xy = transproj.transform(lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    transproj = Transformer.from_crs({"proj":'utm', "zone":'18', "datum":'WGS84'}, {"proj":'latlong', "datum":'WGS84'})
    lonlat = transproj.transform(x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('NY center longitude={}, latitude={}'.format(longitude, latitude))
x_ny, y_ny = lonlat_to_xy(longitude, latitude)
print('NY center UTM X={}, Y={}'.format(x_ny, y_ny))
lo, la = xy_to_lonlat(x_ny, y_ny)
print('NY center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
NY center longitude=-74.0060152, latitude=40.7127281
NY center UTM X=583958.1787429522, Y=4507343.002348409
NY center longitude=-74.0060152, latitude=40.71272809999999


Se calcula la distancia de los barrios hacia el centro de la ciudad de Nueva york.

In [189]:
distance_from_center = []
x11 = []
y11 = []

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']): 
    x1, y1 = lonlat_to_xy(lng, lat)
    distance = calc_xy_distance(x_ny, y_ny, x1, y1)
    distance_from_center.append(distance)
    x11.append(x1)
    y11.append(y1)

#### Crea un mapa de Nueva York con los barrios superpuestos con folium:

In [190]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

#### Foursquare:

Ahora que tenemos nuestros candidatos de ubicación, vamos a utilizar la API de Foursquare para obtener información sobre los restaurantes de cada barrio.

Nos interesan los locales de la categoría "comida", pero sólo los que son restaurantes propiamente dichos; las cafeterías, pizzerías, panaderías, etc. no son competidores directos, por lo que no nos interesan. Así que incluiremos en nuestra lista sólo los locales que tengan "restaurante" en el nombre de la categoría, y nos aseguraremos de detectar e incluir todas las subcategorías de la categoría específica "restaurante japones", ya que necesitamos información sobre los restaurantes japoneses del barrio.

In [191]:
# Category IDs corresponding to japanese restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4bf58dd8d48988d142941735' # 'Root' category for all food-related venues

japanese_restaurant_categories = '4bf58dd8d48988d111941735'

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius, limit):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [192]:
import pickle

foursquare_client_id = ''
foursquare_client_secret = ''

def get_restaurants(lats, lons):
    restaurants = {}
    japanese_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around of neighborhoods:', end='')
    for lat, lon in zip(lats, lons):
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_japanese = is_restaurant(venue_categories, specific_filter=japanese_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_japanese, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_japanese:
                    japanese_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, japanese_restaurants, location_restaurants

In [193]:
restaurants, japanese_restaurants, location_restaurants = get_restaurants(neighborhoods['Latitude'], neighborhoods['Longitude'])

Obtaining venues around of neighborhoods: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [194]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of japanese restaurants:', len(japanese_restaurants))
print('Percentage of japanese restaurants: {:.2f}%'.format(len(japanese_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 1818
Total number of japanese restaurants: 193
Percentage of japanese restaurants: 10.62%
Average number of restaurants in neighborhood: 4.601307189542483


In [195]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4c9d5f2654c8a1cd2e71834b', 'Guang Hui Chinese Restaurant', 40.876651, -73.829092, '125 Dreiser Loop, Bronx, NY 10475, United States', 271, False, 598659.5114999228, 4525724.091301922)
('4dabc3dc93a04642f09ccabd', 'Xing Lung Chinese Restaurant', 40.8887854684858, -73.83122576835156, '3828 B Dyre Ave (E 233 St), Bronx, NY 10466, United States', 318, False, 598461.7311812823, 4527068.7429428175)
('4e4ddf76bd4101d0d79d3e83', 'Panda Restaurant', 40.880013, -73.90440799999999, '5625 Broadway, Bronx, NY 10463, United States', 229, False, 592308.6747716133, 4526015.151729679)
('4b2285c5f964a520454824e3', 'Pioneer Chinese Restaurant', 40.879540999999996, -73.905327, '223 W 231st St (btwn Broadway and Godwin), Bronx, NY 10463, United States', 318, False, 592231.8986733014, 4525961.786214249)
('4c703518b5a5236a2d934f52', 'Kam Wah Kitchen', 40.87608431180527, -73.90869825954931, '5400 Broadway, Bronx, NY 10463, United States', 173, False, 591952.63

In [196]:
print('List of japanese restaurants')
print('---------------------------')
for r in list(japanese_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(japanese_restaurants))

List of japanese restaurants
---------------------------
('4ed9459702d5244e2f1ade7c', 'Empire Chinese And Japanese Cuisine', 40.878588, -73.917446, 'Bronx, NY 10463, United States', 313, True, 591212.1004046419, 4525843.294782097)
('59431675b1ec1308509ffff7', 'Ohana Hibachi Steak & Seafood', 40.828645, -73.824702, '3604 East Tremont Avenue, New York, NY 10465, United States', 262, True, 599100.9312961168, 4520399.899530095)
('54de4db5498ee465b7d151d2', 'Sarku Japan', 40.828769832278994, -73.84824397798991, '815 Hutchinson River Pkwy, Bronx, NY 10465, United States', 223, True, 597115.6537309325, 4520387.397450512)
('4dba07b7fa8c2e303f1b124f', 'Yama Asian Bistro', 40.658578000000006, -73.982259, '268 Prospect Park W, Brooklyn, NY 11215, United States', 258, True, 586034.421135075, 4501354.992041558)
('51f9b7b3498eefe896caeb23', 'Shalom Japan', 40.709219, -73.955839, '310 S 4th St (at Rodney St), Brooklyn, NY 11211, United States', 258, True, 588201.0746759088, 4507002.643504783)
('5b53c

Veamos ahora todos los restaurantes recogidos en nuestra zona de interés en el mapa, y mostremos también los restaurantes japoneses en diferente color.

In [197]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)
folium.Marker([latitude, longitude]).add_to(map_newyork)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_japanese = res[6]
    color = 'red' if is_japanese else 'blue'
    folium.CircleMarker([lat, lon], radius=2, color=color, fill=True, fill_color=color, fill_opacity=0.7).add_to(map_newyork)
map_newyork

Ahora tenemos todos los restaurantes de la zona a pocos kilómetros del centro de la ciudad de Nueva York, y sabemos cuáles son los restaurantes japoneses. También sabemos qué restaurantes están exactamente en las inmediaciones de cada barrio.

Esto concluye la fase de recopilación de datos: ¡ahora vamos a utilizar estos datos para el análisis y elaborar el informe sobre las ubicaciones óptimas para un nuevo restaurante japones!

# 3. Metodología:

En este proyecto dirigiremos nuestros esfuerzos a detectar las zonas de la ciudad de Nueva York que tienen una baja densidad de restaurantes, en particular las que tienen un bajo número de restaurantes japoneses.

El primer paso de nuestro análisis será el cálculo y la exploración de la "densidad de restaurantes" en diferentes zonas de Nueva York. Utilizaremos mapas térmicos para identificar algunas zonas prometedoras cercanas al centro con un bajo número de restaurantes en general (y sin restaurantes japoneses en los alrededores) y centraremos nuestra atención en esas zonas.

En el segundo y último paso nos centraremos en las zonas más prometedoras y, dentro de ellas, ubucaremos los barrios que cumplan los requisitos básicos establecidos en las conversaciones con las partes interesadas: tendremos en cuenta los barrios con no más de dos restaurantes en un radio de 250 metros, y queremos barrios sin restaurantes japoneses en un radio de 400 metros. Presentaremos un mapa de todas esas ubicaciones, pero también crearemos grupos (utilizando la agrupación de k-means) de esas ubicaciones para identificar las zonas/barrios generales que deberían ser la ubicación óptima del barrio por parte de los interesados.

#### Análisis:

Realicemos algunos análisis básicos de datos explicativos y obtengamos alguna información adicional de nuestros datos brutos. En primer lugar, vamos a contar el número de restaurantes en cada barrio:

In [198]:
location_restaurants_count = [len(res) for res in location_restaurants]

neighborhoods['Distance from center'] = distance_from_center
neighborhoods['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

neighborhoods

Average number of restaurants in every area with radius=300m: 4.601307189542483


Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

Bien, ahora vamos a calcular la distancia al restaurante japones más cercano desde el centro de cada zona (no sólo los que están a menos de 300 metros, queremos la distancia al más cercano, independientemente de su distancia.

In [199]:
distances_to_japanese_restaurant = []
   
for area_x, area_y in zip(x11, y11):
    min_distance = 10000
    for res in japanese_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_japanese_restaurant.append(min_distance)

neighborhoods['Distance to japanese restaurant'] = distances_to_japanese_restaurant
neighborhoods['X'] = x11
neighborhoods['Y'] = y11

neighborhoods

Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

In [200]:
print('Average distance to closest japanese restaurant from each area center:', neighborhoods['Distance to japanese restaurant'].mean())

Average distance to closest japanese restaurant from each area center: 2155.460907535487


De acuerdo, por término medio se puede encontrar un restaurante japones a unos 2000 metros al centro de cada zona. Eso está bastante lejos, así que tenemos que filtrar nuestras áreas de otra manera.

Creemos un mapa que muestre la densidad de los restaurantes e intentemos extraer información significativa de él. Además, vamos a mostrar algunos círculos que indican la distancia de 3km, 6km y 9km del centro de la ciudad de Nueva york.

In [201]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

japanese_latlons = [[res[2], res[3]] for res in japanese_restaurants.values()]

In [202]:
from folium import plugins
from folium.plugins import HeatMap

map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)
folium.TileLayer('cartodbpositron').add_to(map_newyork) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_newyork)
folium.Marker([latitude, longitude]).add_to(map_newyork)
folium.Circle([latitude, longitude], radius=3000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=6000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=9000, fill=False, color='white').add_to(map_newyork)
map_newyork

Parece que hay algunos focos de baja densidad de restaurantes más cercanos al centro de la ciudad al este y sur del centro de la ciudad de Nueva York.

Creemos otro mapa de calor que muestre la densidad de los restaurantes japoneses únicamente

In [203]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)
folium.TileLayer('cartodbpositron').add_to(map_newyork) #cartodbpositron cartodbdark_matter
HeatMap(japanese_latlons).add_to(map_newyork)
folium.Marker([latitude, longitude]).add_to(map_newyork)
folium.Circle([latitude, longitude], radius=3000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=6000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=9000, fill=False, color='white').add_to(map_newyork)
map_newyork

Este mapa no es tan "caliente", pero también indica una mayor densidad de restaurantes japoneses existentes directamente al norte del centro de Nueva York, con bolsas más cercanas de baja densidad de restaurantes japoneses situadas al este y sur del centro de la ciudad.

Basándonos en esto, moveremos el centro de nuestra área de interés a brooklyn y nos situaremos principalmente en los barrios de brooklyn, que es una locacion muy importante para abrir un negocio de comida japonesa debido a su alto nivel turistico. Evaluaremos si es posible abrir un restaurante japones en este distrito tan atractivo dentro de los limites que se han establecido. Haciendo un mejor filtro podríamos acercarnos aun más a establecer una mejor locacion para el restaurante japones sin ir muy lejos del centro de la ciudad de Nueva York.

In [204]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data

Borough               Neighborhood   Latitude  Longitude  \
0   Brooklyn                  Bay Ridge  40.625801 -74.030621   
1   Brooklyn                Bensonhurst  40.611009 -73.995180   
2   Brooklyn                Sunset Park  40.645103 -74.010316   
3   Brooklyn                 Greenpoint  40.730201 -73.954241   
4   Brooklyn                  Gravesend  40.595260 -73.973471   
5   Brooklyn             Brighton Beach  40.576825 -73.965094   
6   Brooklyn             Sheepshead Bay  40.586890 -73.943186   
7   Brooklyn          Manhattan Terrace  40.614433 -73.957438   
8   Brooklyn                   Flatbush  40.636326 -73.958401   
9   Brooklyn              Crown Heights  40.670829 -73.943291   
10  Brooklyn              East Flatbush  40.641718 -73.936103   
11  Brooklyn                 Kensington  40.642382 -73.980421   
12  Brooklyn            Windsor Terrace  40.656946 -73.980073   
13  Brooklyn           Prospect Heights  40.676822 -73.964859   
14  Brooklyn                Brownsville  40.663950 -73.910235   
15  Brooklyn               Williamsburg  40.707144 -73.958115   
16  Brooklyn                   Bushwick  40.698116 -73.925258   
17  Brooklyn         Bedford Stuyvesant  40.687232 -73.941785   
18  Brooklyn           Brooklyn Heights  40.695864 -73.993782   
19  Brooklyn                Cobble Hill  40.687920 -73.998561   
20  Brooklyn            Carroll Gardens  40.680540 -73.994654   
21  Brooklyn                   Red Hook  40.676253 -74.012759   
22  Brooklyn                    Gowanus  40.673931 -73.994441   
23  Brooklyn                Fort Greene  40.688527 -73.972906   
24  Brooklyn                 Park Slope  40.672321 -73.977050   
25  Brooklyn              Cypress Hills  40.682391 -73.876616   
26  Brooklyn              East New York  40.669926 -73.880699   
27  Brooklyn              Starrett City  40.647589 -73.879370   
28  Brooklyn                   Canarsie  40.635564 -73.902093   
29  Brooklyn                  Flatlands  40.630446 -73.929113   
30  Brooklyn                Mill Island  40.606336 -73.908186   
31  Brooklyn            Manhattan Beach  40.577914 -73.943537   
32  Brooklyn               Coney Island  40.574293 -73.988683   
33  Brooklyn                 Bath Beach  40.599519 -73.998752   
34  Brooklyn               Borough Park  40.633131 -73.990498   
35  Brooklyn              Dyker Heights  40.619219 -74.019314   
36  Brooklyn            Gerritsen Beach  40.590848 -73.930102   
37  Brooklyn                Marine Park  40.609748 -73.931344   
38  Brooklyn               Clinton Hill  40.693229 -73.967843   
39  Brooklyn                   Sea Gate  40.576375 -74.007873   
40  Brooklyn                   Downtown  40.690844 -73.983463   
41  Brooklyn                Boerum Hill  40.685683 -73.983748   
42  Brooklyn  Prospect Lefferts Gardens  40.658420 -73.954899   
43  Brooklyn                 Ocean Hill  40.678403 -73.913068   
44  Brooklyn                  City Line  40.678570 -73.867976   
45  Brooklyn               Bergen Beach  40.615150 -73.898556   
46  Brooklyn                    Midwood  40.625596 -73.957595   
47  Brooklyn        Prospect Park South  40.647009 -73.962613   
48  Brooklyn                 Georgetown  40.623845 -73.916075   
49  Brooklyn          East Williamsburg  40.708492 -73.938858   
50  Brooklyn                 North Side  40.714823 -73.958809   
51  Brooklyn                 South Side  40.710861 -73.958001   
52  Brooklyn              Ocean Parkway  40.613060 -73.968367   
53  Brooklyn              Fort Hamilton  40.614768 -74.031979   
54  Brooklyn                Ditmas Park  40.643675 -73.961013   
55  Brooklyn                    Wingate  40.660947 -73.937187   
56  Brooklyn                      Rugby  40.655572 -73.926882   
57  Brooklyn             Remsen Village  40.652117 -73.916653   
58  Brooklyn                   New Lots  40.662744 -73.885118   
59  Brooklyn            Paerdegat Basin  40.631318 -73.902335   
60  Brooklyn                 Mill Basin 

In [205]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude_b = location.latitude
longitude_b = location.longitude
print('The geograpical coordinate of brooklyn are {}, {}.'.format(latitude_b, longitude_b))

The geograpical coordinate of brooklyn are 40.6501038, -73.9495823.


In [206]:
map_brooklyn = folium.Map(location=[latitude_b, longitude_b], zoom_start=12)

for lat, lng, label in zip(brooklyn_data['Latitude'], brooklyn_data['Longitude'], brooklyn_data['Neighborhood']):
    folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_brooklyn)  
map_brooklyn

Se calculan las ubicaciones en un sistema de coordenadas cartesianas 2D que nos permita calcular las distancias en metros.

In [207]:
x22 = []
y22 = []

for lat, lng in zip(brooklyn_data['Latitude'], brooklyn_data['Longitude']):
    x2, y2 = lonlat_to_xy(lng, lat)
    x22.append(x2)
    y22.append(y2)

Bien. Ahora vamos a calcular las dos cosas más importantes para cada barrio a ubicación: el número de restaurantes en los alrededores (utilizaremos un radio de 250 metros) y la distancia al restaurante japones más cercano.

In [208]:
def count_restaurants_nearby(x, y, restaurants, radius):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 10000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_japanese_distances = []

print('Generating data on location candidates... ', end='')
for xa, ya in zip(x22, y22):
    count = count_restaurants_nearby(xa, ya, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(xa, ya, japanese_restaurants)
    roi_japanese_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [209]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Neighborhood':brooklyn_data['Neighborhood'],
                                 'Latitude':brooklyn_data['Latitude'],
                                 'Longitude':brooklyn_data['Longitude'],
                                 'X':x22,
                                 'Y':y22,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Japanese restaurant':roi_japanese_distances})

df_roi_locations

Neighborhood   Latitude  Longitude              X  \
0                   Bay Ridge  40.625801 -74.030621  581986.217481   
1                 Bensonhurst  40.611009 -73.995180  585002.446210   
2                 Sunset Park  40.645103 -74.010316  583679.412722   
3                  Greenpoint  40.730201 -73.954241  588308.331222   
4                   Gravesend  40.595260 -73.973471  586859.338213   
5              Brighton Beach  40.576825 -73.965094  587592.164808   
6              Sheepshead Bay  40.586890 -73.943186  589433.042417   
7           Manhattan Terrace  40.614433 -73.957438  588190.735274   
8                    Flatbush  40.636326 -73.958401  588080.532314   
9               Crown Heights  40.670829 -73.943291  589312.263119   
10              East Flatbush  40.641718 -73.936103  589958.950277   
11                 Kensington  40.642382 -73.980421  586210.633134   
12            Windsor Terrace  40.656946 -73.980073  586221.284337   
13           Prospect Heights  40.676822 -73.964859  587481.482039   
14                Brownsville  40.663950 -73.910235  592115.634691   
15               Williamsburg  40.707144 -73.958115  588011.522916   
16                   Bushwick  40.698116 -73.925258  590799.401047   
17         Bedford Stuyvesant  40.687232 -73.941785  589417.654809   
18           Brooklyn Heights  40.695864 -73.993782  585012.908728   
19                Cobble Hill  40.687920 -73.998561  584619.174886   
20            Carroll Gardens  40.680540 -73.994654  584958.739292   
21                   Red Hook  40.676253 -74.012759  583434.042216   
22                    Gowanus  40.673931 -73.994441  584985.120695   
23                Fort Greene  40.688527 -73.972906  586786.262647   
24                 Park Slope  40.672321 -73.977050  586456.993967   
25              Cypress Hills  40.682391 -73.876616  594931.308144   
26              East New York  40.669926 -73.880699  594603.917130   
27              Starrett City  40.647589 -73.879370  594747.843553   
28                   Canarsie  40.635564 -73.902093  592843.268556   
29                  Flatlands  40.630446 -73.929113  590565.200187   
30                Mill Island  40.606336 -73.908186  592368.266197   
31            Manhattan Beach  40.577914 -73.943537  589415.307221   
32               Coney Island  40.574293 -73.988683  585598.882814   
33                 Bath Beach  40.599519 -73.998752  584714.757698   
34               Borough Park  40.633131 -73.990498  585370.332300   
35              Dyker Heights  40.619219 -74.019314  582950.669651   
36            Gerritsen Beach  40.590848 -73.930102  590535.018343   
37                Marine Park  40.609748 -73.931344  590404.422307   
38               Clinton Hill  40.693229 -73.967843  587207.919235   
39                   Sea Gate  40.576375 -74.007873  583971.979199   
40                   Downtown  40.690844 -73.983463  585891.186398   
41                Boerum Hill  40.685683 -73.983748  585873.742076   
42  Prospect Lefferts Gardens  40.658420 -73.954899  588347.565319   
43                 Ocean Hill  40.678403 -73.913068  591856.328762   
44                  City Line  40.678570 -73.867976  595666.905786   
45               Bergen Beach  40.615150 -73.898556  593170.691089   
46                    Midwood  40.625596 -73.957595  588162.789410   
47        Prospect Park South  40.647009 -73.962613  587710.353263   
48                 Georgetown  40.623845 -73.916075  591676.890237   
49          East Williamsburg  40.708492 -73.938858  589636.458785   
50                 North Side  40.714823 -73.958809  587942.853951   
51                 South Side  40.710861 -73.958001  588016.287007   
52              Ocean Parkway  40.613060 -73.968367  587268.070022   
53              Fort Hamilton  40.614768 -74.031979  581884.795797   
54                Ditmas Park  40.643675 -73.961013  587850.009245   
55                    Wingate  40.660947 -73.937187  589841.472520   
56                      Rug

Ahora vamos a filtrar esos lugares: sólo nos interesan los barrios con no más de dos restaurantes en un radio de 250 metros, y ningún restaurante japones en un radio de 400 metros.

In [210]:
good_restaurant_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Neighborhood with no more than two restaurants nearby:', good_restaurant_count.sum())

good_japanese_distance = np.array(df_roi_locations['Distance to Japanese restaurant']>=400)
print('Neighborhood with no Japanese restaurants within 400m:', good_japanese_distance.sum())

good_locations = np.logical_and(good_restaurant_count, good_japanese_distance)
print('Neighborhood with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Neighborhood with no more than two restaurants nearby: 49
Neighborhood with no Japanese restaurants within 400m: 50
Neighborhood with both conditions met: 41


Veamos cómo se ve esto en un mapa.

In [211]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values
good_neighborhood = df_good_locations['Neighborhood'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_brooklyn = folium.Map(location=[latitude_b, longitude_b], zoom_start=12)
folium.TileLayer('cartodbpositron').add_to(map_brooklyn)
HeatMap(good_locations, radius=70).add_to(map_brooklyn)
folium.Marker([latitude, longitude]).add_to(map_brooklyn)
folium.Marker([latitude_b, longitude_b]).add_to(map_brooklyn)
for lat, lon, label in zip(good_latitudes, good_longitudes, good_neighborhood):
    folium.Popup(label)
    folium.CircleMarker([lat, lon], radius=2, popup=label, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_brooklyn) 
map_brooklyn

Ahora tenemos un grupo de barrios en la esquina sureste en el distrito de brooklin, y sabemos que cada una de esas ubicaciones no tiene más de dos restaurantes en un radio de 250 metros, y ningún restaurante italiano más cerca de 400 metros. Cualquiera de esos lugares es un candidato potencial para un nuevo restaurante japones, al menos en función de la competencia cercana.

Agrupemos ahora esos barrios para crear centros de zonas que contengan buenos lugares. Esas zonas, sus centros y sus distancias del centro de la ciudad serán el resultado final de nuestro análisis.

In [212]:
from sklearn.cluster import KMeans

number_of_clusters = 9

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_brooklyn = folium.Map(location=[latitude_b, longitude_b], zoom_start=12)
folium.TileLayer('cartodbpositron').add_to(map_brooklyn)
HeatMap(good_locations, radius=70).add_to(map_brooklyn)
folium.Marker([latitude, longitude]).add_to(map_brooklyn)
folium.Marker([latitude_b, longitude_b]).add_to(map_brooklyn)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=2500, color='green', fill=True, fill_opacity=0.25).add_to(map_brooklyn) 
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_japanese = res[6]
    color = 'red' if is_japanese else 'blue'
    folium.CircleMarker([lat, lon], radius=2, color=color, fill=True, fill_color=color, fill_opacity=0.7).add_to(map_brooklyn) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=5, color='yellow', fill=True, fill_color='yellow', fill_opacity=0.7).add_to(map_brooklyn)
map_brooklyn

Nuestros clústeres representan agrupaciones de la mayoría de las ubicaciones candidatas y los centros de los clústeres están bien situados en el centro de los barrios candidatos a ubicación del reutarante japones.

Veamos esas zonas en un mapa de la ciudad sin mapa de calor, utilizando puntos para indicar nuestros barrios seleccionados y marcadores para los centros de los clusters:

In [213]:
map_brooklyn = folium.Map(location=[latitude_b, longitude_b], zoom_start=12)
folium.Circle([latitude, longitude], radius=250, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_brooklyn)
for latlon, i in zip (cluster_centers, range(len(cluster_centers))):
    folium.Marker([latlon[1], latlon[0]], popup='Cluster' + str(i)).add_to(map_brooklyn)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.5).add_to(map_brooklyn)
map_brooklyn

Con esto concluye nuestro análisis. Hemos creado 9 clusters que representan los centros de las zonas que contienen lugares con escaso número de restaurantes y sin restaurantes japoneses cerca, estando algunas de las zonas bastante cerca del centro de la ciudad de Nueva York. Las zonas que se muestran en el mapa deben considerarse sólo como un punto de partida para explorar los barrios de la zona en busca de posibles restaurantes. La mayoría de las zonas se encuentran en los barrios de brooklyn, que hemos identificado como interesantes por ser populares entre los turistas, estar bastante cerca del centro de la ciudad.

In [214]:
for latlon, i in zip (cluster_centers, range(len(cluster_centers))): 
    x33, y33 = lonlat_to_xy(latlon[0], latlon[1])
    dist = calc_xy_distance(x33, y33, x_ny, y_ny)
    print('{}{} => {:.1f}km from New York center'.format('Cluster ', i, dist/1000))

Cluster 0 => 11.6km from New York center
Cluster 1 => 13.4km from New York center
Cluster 2 => 4.6km from New York center
Cluster 3 => 9.7km from New York center
Cluster 4 => 12.8km from New York center
Cluster 5 => 15.3km from New York center
Cluster 6 => 8.8km from New York center
Cluster 7 => 8.9km from New York center
Cluster 8 => 4.2km from New York center


# 4. Resultados y discusión 

Nuestro análisis muestra que, aunque hay un gran número de restaurantes en Nueva York, hay bolsas de baja densidad de restaurantes bastante cerca del centro de la ciudad. La mayor concentración de restaurantes se detectó al norte del centro de la ciudad de Nueva York, por lo que centramos nuestra atención en las zonas del sur y sureste, correspondientes a los barrios de brooklyn que ofrecen una combinación de popularidad entre los turistas, cercanía al centro de la ciudad, fuerte dinámica socioeconómica y varias bolsas de baja densidad de restaurantes.

Tras centrar nuestra atención en esta zona de interés más reducida, se filtraron los lugares con más de dos restaurantes en un radio de 250 m y los que tenían un restaurante japones a menos de 400 m.

A continuación, se agruparon esos candidatos a ubicación para crear zonas de interés que contienen el mayor número de candidatos a ubicación. También se generaron las distancias a los centros de esas zonas como marcadores/puntos de partida para un análisis local más detallado basado en otros factores.

El resultado de todo esto son 9 zonas que contienen el mayor número de posibles nuevas ubicaciones de restaurantes en función del número y la distancia a los locales existentes, tanto de restaurantes en general como de restaurantes japoneses en particular. Esto, por supuesto, no implica que esas zonas sean realmente los lugares óptimos para un nuevo restaurante. El objetivo de este análisis era proporcionar sólo información sobre las zonas cercanas al centro de Nueva York pero que no están abarrotadas de restaurantes existentes (especialmente japoneses) - es totalmente posible que haya una muy buena razón para el pequeño número de restaurantes en cualquiera de esas zonas, razones que las harían inadecuadas para un nuevo restaurante independientemente de la falta de competencia en la zona. Por lo tanto, las zonas recomendadas deben considerarse sólo como un punto de partida para un análisis más detallado que podría acabar dando como resultado una ubicación que no sólo no tenga competencia cercana, sino que también se tengan en cuenta otros factores y se cumplan todas las demás condiciones pertinentes.

# 5. Conclusión 

El objetivo de este proyecto era identificar los barrios de Nueva York cercanas al centro con un bajo número de restaurantes (en particular, restaurantes japoneses) para ayudar a los interesados a reducir la búsqueda de la ubicación óptima para un nuevo restaurante japones. Mediante el cálculo de la distribución de la densidad de restaurantes a partir de los datos de Foursquare, hemos identificado en primer lugar los barrios generales que justifican un análisis más profundo (brooklyn) y, a continuación, hemos generado una amplia colección de ubicaciones que satisfacen algunos requisitos básicos relativos a los restaurantes cercanos existentes. A continuación, se han agrupado estos lugares para crear las principales zonas de interés (que contienen el mayor número de locales potenciales para establecer un restaurante japones) y se han creado las distancias de los centros de estas zonas para utilizarlas como puntos de partida para la exploración final por parte de los interesados.

Las partes interesadas tomarán la decisión final sobre la ubicación óptima de los restaurantes basándose en las características específicas de los barrios y las ubicaciones de cada zona recomendada, teniendo en cuenta factores adicionales como proximidad a un parque o a carreteras principales, la disponibilidad inmobiliaria, los precios, la dinámica social y económica de cada barrio, etc.